## Table of Contents

[1. Import News Data](#Import)<br>
[2. Sentiment Analysis](#Sentiment)<br>
&emsp;&emsp;[2.1 Harvard IV-4 Dictionary](#Harvard)<br>
&emsp;&emsp;[2.2 Loughran and McDonald Dictionary](#Maccy)<br>
[3. Notes](#Notes)<br>

In [1]:
# Import libraries 
import numpy as np
import pandas as pd
import os

from datetime import datetime

<a id='Import'></a>
## Import News Data

In [2]:
zip_lst = ['Data1.zip', 'Data2.zip', 'Data3.zip']
df_news = pd.DataFrame()

for zip_dt in zip_lst:
    df_news = pd.concat([df_news, pd.read_csv(zip_dt)], axis=0)

# Remove entries without content
df_news['content'].replace('empty string', np.nan, inplace=True)
df_news = df_news.loc[~df_news['content'].isna(), ]

# Reset index
df_news.reset_index(drop=True, inplace=True)

df_news.shape

(38515, 7)

In [3]:
df_news.head(10)

ticker       date     time  \
0    MMM  Feb-19-21  08:11AM   
1    MMM  Feb-18-21  11:00AM   
2    MMM  Feb-17-21  09:37AM   
3    MMM  Feb-16-21  04:18PM   
4    MMM  Feb-16-21  03:58PM   
5    MMM  Feb-16-21  08:00AM   
6    MMM  Feb-12-21  05:12PM   
7    MMM  Feb-09-21  02:35PM   
8    MMM  Feb-09-21  11:07AM   
9    MMM  Feb-09-21  11:07AM   

                                            headline                  news  \
0  Did You Acquire 3M (MMM) Before February 9, 20...           PR Newswire   
1  3M launches New 3M Clean & Protect Certified B...           PR Newswire   
2                               ROCE Insights For 3M              Benzinga   
3  Why 3M is spending $1 billion to help improve ...         Yahoo Finance   
4  3M CEO on the company's plans to invest $1B to...   Yahoo Finance Video   
5  3M to Invest $1 Billion to Achieve Carbon Neut...           PR Newswire   
6    First Eagle Investment's Top 4th-Quarter Trades         GuruFocus.com   
7              3M Announces Upcoming Investor Events           PR Newswire   
8  New 3M Polisher ST reduces the number of bioph...           PR Newswire   
9  New 3M Polisher ST reduces the number of bioph...             CNW Group   

                                             content               site  
0  SAN DIEGO, Feb. 19, 2021 /PRNewswire/ -- Johns...  finance.yahoo.com  
1  The new four-part program promotes cleanliness...  finance.yahoo.com  
2  3M (NYSE:MMM) posted a 3.14% decrease in earni...  finance.yahoo.com  
3  3M Chairman and CEO Mike Roman said it's time ...  finance.yahoo.com  
4  Mike Roman, 3M Chairman and CEO, joined Yahoo ...  finance.yahoo.com  
5  ST. PAUL, Minn., Feb. 16, 2021 /PRNewswire/ --...  finance.yahoo.com  
6  - By Graham GriffinFirst Eagle Investment (Tra...  finance.yahoo.com  
7  ST. PAUL, Minn., Feb. 9, 2021 /PRNewswire/ -- ...  finance.yahoo.com  
8  ST. PAUL, Minn., Feb. 9, 2021 /PRNewswire/ -- ...  finance.yahoo.com  
9  ST. PAUL, Minn., Feb. 9, 2021 /CNW/ -- 3M Heal...  finance.yahoo.com

In [4]:
# Import labelled validation data 
valid = pd.read_csv('data/news_sample.csv', index_col=0)
valid.head()

ticker       date     time  \
3174      PM  Feb-04-21  10:33AM   
8657    CTLT  Sep-09-20  10:14AM   
16599    ZTS  Feb-12-21  08:38AM   
5695     AZO  Sep-18-20  06:25AM   
7327     SEE  May-28-20  09:08AM   

                                                headline              news  \
3174   Philip Morris (PM) Q4 Earnings Beat Estimates ...             Zacks   
8657   Radius Completes Enrollment in Phase III Osteo...             Zacks   
16599  Is a Surprise Coming for Zoetis (ZTS) This Ear...             Zacks   
5695   If You Had Bought AutoZone (NYSE:AZO) Shares T...   Simply Wall St.   
7327   Sealed Air (SEE) Stock Down 18% YTD: Will it B...             Zacks   

                                                 content               site  \
3174   Philip Morris International Inc. PM reported f...  finance.yahoo.com   
8657   Radius Health, Inc. RDUS announced the complet...  finance.yahoo.com   
16599  Investors are always looking for stocks that a...  finance.yahoo.com   
5695   The worst result, after buying shares in a com...  finance.yahoo.com   
7327   Sealed Air Corporation’s SEE focus on innovati...  finance.yahoo.com   

       sent  
3174      1  
8657      1  
16599     1  
5695      1  
7327      0

<a id='Sentiment'></a>
## Sentiment Analysis

In [5]:
# Pysentiment contains 2 dictionaries- Harvard and Loughran and Mcdonald
import pysentiment2 as ps
import math
from statistics import variance 
from scipy.stats import spearmanr

<a id='Harvard'></a>
### Harvard Sentiment Analysis

#### Using headlines

In [6]:
# Data exploration- sentiment for each headline
hiv4 = ps.HIV4()
# Text is pre-processed by default tokenizer in library
for i in df_news['headline']:
    tokens = hiv4.tokenize(i)
    score = hiv4.get_score(tokens)
    print(score)

{'Positive': 3, 'Negative': 1, 'Polarity': 0.49999987500003124, 'Subjectivity': 0.3636363305785154}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.24999996875000394}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.33333322222225925}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.33333327777778704}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.09090908264462885}
{'Positive': 4, 'Negative': 1, 'Polarity': 0.599999880000024, 'Subjectivity': 0.6249999218750099}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{

{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.09999999000000101}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.285714244897965}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.24999996875000394}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.399999920000016

{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.33333327777778704}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.6666664444445185}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.399999920000016}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.33333327777778704}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.09090908264462885}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.499999750000125}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 3, 'Negative': 0, 'Polarity': 0.9999996666667778, 'Subjectivity': 0.599999880000024}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.399999920000016}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.49999987500003124}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.33333322222225925}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'S

{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 0, 'Negative': 2, 'Polarity': -0.99999950000025, 'Subjectivity': 0.399999920000016}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.33333322222225925}
{'Positive': 0, 'Negative': 2, 'Polarity': -0.99999950000025, 'Subjectivity': 0.399999920000016}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.33333322222225925}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.09999999000000101}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'

...

{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.11111109876543349}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.24999996875000394}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.33333322222225925}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.2222221975

{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.22222219753086697}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.33333327777778704}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.285714244897965}
{'Positive': 0, 'Negative': 2, 'Polarity': -0.99999950000025, 'Subjectivity': 0.24999996875000394}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'Positive': 0, 'Negative': 2, 'Polarity': -0.99999950000025, 'Subjectivity': 0.285714244897965}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Su

{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.285714244897965}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.33333322222225925}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 3, 'Negative': 0, 'Polarity': 0.9999996666667778, 'Subjectivity': 0.599999880000024}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 2, 'Polarity': -0.99999950000025, 'Subjectivity': 0.399999920000016}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.09999999000000101}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Po

{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.24999996875000394}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.11764705190311459}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.09999999000000101}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.24999996875000394}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivit

{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.285714244897965}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.22222219753086697}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.12499999218750048}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 2, 'Negative': 1, 'Polarity': 0.33333322222225925, 'Subjectivity': 0.21428569897959293}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.24999993750001562}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.33333327777778704}
{'Positive': 0,

- The Havard IV dictionary returns word counts for the number of positive and negative words that occur within the specified text. Polarity is calculated as Polarity = (Pos-Neg) / (Pos+Neg), and Subjectivity = (Pos+Neg) / count(*).

- Source: [Link](https://nickderobertis.github.io/pysentiment/)

In [7]:
# Predict sentiment score from labelled data
scores = []
for i in valid['headline']:
    tokens = hiv4.tokenize(i)
    score = hiv4.get_score(tokens)
    scores.append(score['Polarity']) # Take only polarity score as proxy for sentiment
    
sc = np.asarray(scores)
# Add to validation dataframe
valid['score'] = sc
valid.head()

ticker       date     time  \
3174      PM  Feb-04-21  10:33AM   
8657    CTLT  Sep-09-20  10:14AM   
16599    ZTS  Feb-12-21  08:38AM   
5695     AZO  Sep-18-20  06:25AM   
7327     SEE  May-28-20  09:08AM   

                                                headline              news  \
3174   Philip Morris (PM) Q4 Earnings Beat Estimates ...             Zacks   
8657   Radius Completes Enrollment in Phase III Osteo...             Zacks   
16599  Is a Surprise Coming for Zoetis (ZTS) This Ear...             Zacks   
5695   If You Had Bought AutoZone (NYSE:AZO) Shares T...   Simply Wall St.   
7327   Sealed Air (SEE) Stock Down 18% YTD: Will it B...             Zacks   

                                                 content               site  \
3174   Philip Morris International Inc. PM reported f...  finance.yahoo.com   
8657   Radius Health, Inc. RDUS announced the complet...  finance.yahoo.com   
16599  Investors are always looking for stocks that a...  finance.yahoo.com   
5695   The worst result, after buying shares in a com...  finance.yahoo.com   
7327   Sealed Air Corporation’s SEE focus on innovati...  finance.yahoo.com   

       sent     score  
3174      1 -0.999999  
8657      1  0.000000  
16599     1  0.999999  
5695      1  0.999999  
7327      0  0.000000

In [12]:
# Labelled sentiment
valid['sent'].head()

3174     1
8657     1
16599    1
5695     1
7327     0
Name: sent, dtype: int64

In [13]:
# Predicted sentiment
valid['score'].head()

3174    -0.999999
8657     0.000000
16599    0.999999
5695     0.999999
7327     0.000000
Name: score, dtype: float64

In [16]:
# Calculate correlation between predicted and true 
valid['sent'].corr(valid['score'])

0.05009187128188563

In [19]:
# Check if the variance is zero 
math.sqrt(variance(valid['sent']))

0.7034546786030247

In [20]:
math.sqrt(variance(valid['score']))

0.711480102219824

In [21]:
# Carry out same execution using scipy 
spearmanr(valid['sent'], valid['score'])

SpearmanrResult(correlation=-0.02945148415984825, pvalue=0.771146798057911)

#### Using article content

- A much more granular measure of polarity and subjectivity is obtained.

In [10]:
hiv4 = ps.HIV4()
# Text is pre-processed by default tokenizer in library
for i in df_news['content']:
    tokens = hiv4.tokenize(i)
    score = hiv4.get_score(tokens)
    print(score)

{'Positive': 52, 'Negative': 14, 'Polarity': 0.5757575670339763, 'Subjectivity': 0.31428571278911566}
{'Positive': 136, 'Negative': 9, 'Polarity': 0.8758620629250893, 'Subjectivity': 0.3929539284743796}
{'Positive': 50, 'Negative': 6, 'Polarity': 0.7857142716836738, 'Subjectivity': 0.3499999978125}
{'Positive': 45, 'Negative': 15, 'Polarity': 0.4999999916666668, 'Subjectivity': 0.20134228120354938}
{'Positive': 126, 'Negative': 36, 'Polarity': 0.5555555521262003, 'Subjectivity': 0.2519440120498538}
{'Positive': 256, 'Negative': 54, 'Polarity': 0.6516129011238293, 'Subjectivity': 0.3163265302894627}
{'Positive': 122, 'Negative': 25, 'Polarity': 0.659863941089361, 'Subjectivity': 0.21459853983270286}
{'Positive': 17, 'Negative': 3, 'Polarity': 0.6999999650000017, 'Subjectivity': 0.18691588610358986}
{'Positive': 84, 'Negative': 7, 'Polarity': 0.8461538368554523, 'Subjectivity': 0.3297101437329343}
{'Positive': 89, 'Negative': 7, 'Polarity': 0.8541666577690974, 'Subjectivity': 0.311688310

{'Positive': 79, 'Negative': 27, 'Polarity': 0.4905660331078676, 'Subjectivity': 0.2465116273336939}
{'Positive': 33, 'Negative': 7, 'Polarity': 0.6499999837500005, 'Subjectivity': 0.26845637403720557}
{'Positive': 77, 'Negative': 28, 'Polarity': 0.46666666222222225, 'Subjectivity': 0.2884615376690617}
{'Positive': 75, 'Negative': 26, 'Polarity': 0.48514851004803455, 'Subjectivity': 0.2845070414520928}
{'Positive': 66, 'Negative': 23, 'Polarity': 0.4831460619871229, 'Subjectivity': 0.2564841491167604}
{'Positive': 91, 'Negative': 26, 'Polarity': 0.5555555508072175, 'Subjectivity': 0.2896039596791981}
{'Positive': 100, 'Negative': 25, 'Polarity': 0.5999999952, 'Subjectivity': 0.2723311540907818}
{'Positive': 86, 'Negative': 30, 'Polarity': 0.482758616527943, 'Subjectivity': 0.28999999927500003}
{'Positive': 95, 'Negative': 50, 'Polarity': 0.31034482544589775, 'Subjectivity': 0.2725563904651196}
{'Positive': 81, 'Negative': 33, 'Polarity': 0.4210526278855033, 'Subjectivity': 0.2760290550

{'Positive': 105, 'Negative': 45, 'Polarity': 0.39999999733333336, 'Subjectivity': 0.2604166662145544}
{'Positive': 433, 'Negative': 184, 'Polarity': 0.40356563954041225, 'Subjectivity': 0.28019981821970946}
{'Positive': 108, 'Negative': 64, 'Polarity': 0.2558139520010817, 'Subjectivity': 0.2582582578704831}
{'Positive': 186, 'Negative': 48, 'Polarity': 0.589743587223318, 'Subjectivity': 0.2535211264858926}
{'Positive': 30, 'Negative': 6, 'Polarity': 0.6666666481481487, 'Subjectivity': 0.1698113199537202}
{'Positive': 107, 'Negative': 52, 'Polarity': 0.34591194750998777, 'Subjectivity': 0.23555555520658436}
{'Positive': 308, 'Negative': 155, 'Polarity': 0.33045356300118023, 'Subjectivity': 0.2751039808228734}
{'Positive': 33, 'Negative': 9, 'Polarity': 0.5714285578231296, 'Subjectivity': 0.19626168132587998}
{'Positive': 51, 'Negative': 9, 'Polarity': 0.6999999883333335, 'Subjectivity': 0.20905923272104798}
{'Positive': 89, 'Negative': 40, 'Polarity': 0.3798449582957755, 'Subjectivity'

{'Positive': 323, 'Negative': 79, 'Polarity': 0.6069651726194897, 'Subjectivity': 0.31904761879440663}
{'Positive': 59, 'Negative': 20, 'Polarity': 0.4936708798269509, 'Subjectivity': 0.22128851478630668}
{'Positive': 38, 'Negative': 17, 'Polarity': 0.3818181748760332, 'Subjectivity': 0.21235521153530806}
{'Positive': 22, 'Negative': 11, 'Polarity': 0.33333332323232356, 'Subjectivity': 0.35483870586194943}
{'Positive': 268, 'Negative': 76, 'Polarity': 0.5581395332612223, 'Subjectivity': 0.3071428568686224}
{'Positive': 86, 'Negative': 7, 'Polarity': 0.849462356457394, 'Subjectivity': 0.2915360492428337}
{'Positive': 223, 'Negative': 68, 'Polarity': 0.5326460462795669, 'Subjectivity': 0.3102345412470847}
{'Positive': 50, 'Negative': 5, 'Polarity': 0.8181818033057854, 'Subjectivity': 0.2444444433580247}
{'Positive': 103, 'Negative': 14, 'Polarity': 0.7606837541821901, 'Subjectivity': 0.27400468319905225}
{'Positive': 169, 'Negative': 42, 'Polarity': 0.60189573174457, 'Subjectivity': 0.31

{'Positive': 54, 'Negative': 38, 'Polarity': 0.17391304158790172, 'Subjectivity': 0.2830769222059172}
{'Positive': 53, 'Negative': 38, 'Polarity': 0.16483516302378942, 'Subjectivity': 0.2826086947745072}
{'Positive': 40, 'Negative': 8, 'Polarity': 0.6666666527777781, 'Subjectivity': 0.2651933687005891}
{'Positive': 37, 'Negative': 13, 'Polarity': 0.47999999040000024, 'Subjectivity': 0.23148148040980795}
{'Positive': 93, 'Negative': 30, 'Polarity': 0.5121951177870315, 'Subjectivity': 0.243083003472168}
{'Positive': 105, 'Negative': 44, 'Polarity': 0.4093959704067385, 'Subjectivity': 0.22473604792649163}
{'Positive': 47, 'Negative': 8, 'Polarity': 0.7090908961983474, 'Subjectivity': 0.25462962845078874}
{'Positive': 50, 'Negative': 9, 'Polarity': 0.6949152424590637, 'Subjectivity': 0.22014925290989085}
{'Positive': 13, 'Negative': 3, 'Polarity': 0.6249999609375024, 'Subjectivity': 0.20253164300592857}
{'Positive': 32, 'Negative': 26, 'Polarity': 0.10344827407847804, 'Subjectivity': 0.231

...

{'Positive': 300, 'Negative': 107, 'Polarity': 0.47420147303636, 'Subjectivity': 0.2820512818558203}
{'Positive': 27, 'Negative': 8, 'Polarity': 0.5428571273469392, 'Subjectivity': 0.20588235173010383}
{'Positive': 15, 'Negative': 2, 'Polarity': 0.7647058373702448, 'Subjectivity': 0.16666666503267977}
{'Positive': 70, 'Negative': 9, 'Polarity': 0.7721518889601027, 'Subjectivity': 0.22507122442999652}
{'Positive': 58, 'Negative': 3, 'Polarity': 0.9016393294813225, 'Subjectivity': 0.22676579841351005}
{'Positive': 34, 'Negative': 3, 'Polarity': 0.8378378151935726, 'Subjectivity': 0.27611940092448206}
{'Positive': 38, 'Negative': 27, 'Polarity': 0.16923076662721898, 'Subjectivity': 0.20833333266559828}
{'Positive': 124, 'Negative': 16, 'Polarity': 0.7714285659183674, 'Subjectivity': 0.261194029363444}
{'Positive': 54, 'Negative': 12, 'Polarity': 0.6363636267217633, 'Subjectivity': 0.25984251866203734}
{'Positive': 77, 'Negative': 9, 'Polarity': 0.7906976652244457, 'Subjectivity': 0.245014

{'Positive': 40, 'Negative': 7, 'Polarity': 0.7021276446355821, 'Subjectivity': 0.22380952274376417}
{'Positive': 72, 'Negative': 18, 'Polarity': 0.5999999933333334, 'Subjectivity': 0.2931596081656039}
{'Positive': 112, 'Negative': 21, 'Polarity': 0.6842105211713495, 'Subjectivity': 0.24675324629544854}
{'Positive': 62, 'Negative': 33, 'Polarity': 0.3052631546814405, 'Subjectivity': 0.22352941123875433}
{'Positive': 32, 'Negative': 22, 'Polarity': 0.18518518175583, 'Subjectivity': 0.24657534133983863}
{'Positive': 36, 'Negative': 8, 'Polarity': 0.6363636219008268, 'Subjectivity': 0.2146341452944676}
{'Positive': 150, 'Negative': 42, 'Polarity': 0.5624999970703125, 'Subjectivity': 0.2573726538104924}
{'Positive': 41, 'Negative': 3, 'Polarity': 0.863636344008265, 'Subjectivity': 0.23404255194658216}
{'Positive': 40, 'Negative': 6, 'Polarity': 0.7391304187145562, 'Subjectivity': 0.2804878031677573}
{'Positive': 91, 'Negative': 23, 'Polarity': 0.5964912228377963, 'Subjectivity': 0.24782608

{'Positive': 1023, 'Negative': 569, 'Polarity': 0.2851758792178543, 'Subjectivity': 0.33707389364025536}
{'Positive': 53, 'Negative': 10, 'Polarity': 0.6825396717057195, 'Subjectivity': 0.3165829129819954}
{'Positive': 31, 'Negative': 6, 'Polarity': 0.6756756574141715, 'Subjectivity': 0.2067039094597547}
{'Positive': 57, 'Negative': 27, 'Polarity': 0.35714285289115655, 'Subjectivity': 0.18025751034279505}
{'Positive': 43, 'Negative': 15, 'Polarity': 0.48275861236623085, 'Subjectivity': 0.20567375813590866}
{'Positive': 66, 'Negative': 24, 'Polarity': 0.46666666148148156, 'Subjectivity': 0.23746701784309493}
{'Positive': 32, 'Negative': 5, 'Polarity': 0.7297297100073051, 'Subjectivity': 0.2913385803831608}
{'Positive': 65, 'Negative': 6, 'Polarity': 0.830985903788931, 'Subjectivity': 0.27413127307285223}
{'Positive': 22, 'Negative': 18, 'Polarity': 0.09999999750000006, 'Subjectivity': 0.16528925551533366}
{'Positive': 40, 'Negative': 26, 'Polarity': 0.21212120890725442, 'Subjectivity': 

{'Positive': 88, 'Negative': 20, 'Polarity': 0.6296296237997258, 'Subjectivity': 0.3085714276897959}
{'Positive': 102, 'Negative': 19, 'Polarity': 0.6859504075541288, 'Subjectivity': 0.21684587774758804}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.11764705190311459}
{'Positive': 33, 'Negative': 6, 'Polarity': 0.6923076745562136, 'Subjectivity': 0.24223602334014893}
{'Positive': 83, 'Negative': 20, 'Polarity': 0.611650479498539, 'Subjectivity': 0.3130699078630094}
{'Positive': 116, 'Negative': 28, 'Polarity': 0.611111106867284, 'Subjectivity': 0.23920265740996235}
{'Positive': 134, 'Negative': 26, 'Polarity': 0.67499999578125, 'Subjectivity': 0.2431610938553783}
{'Positive': 104, 'Negative': 19, 'Polarity': 0.6910569049507569, 'Subjectivity': 0.23207547126023495}
{'Positive': 41, 'Negative': 8, 'Polarity': 0.6734693740108292, 'Subjectivity': 0.2112068956413496}
{'Positive': 59, 'Negative': 46, 'Polarity': 0.1238095226303855, 'Subjectivity': 0.10824742256881709}
{'P

KeyboardInterrupt: 

In [22]:
# Predict sentiment score from labelled data
scores_content = []
for i in valid['content']:
    tokens = hiv4.tokenize(i)
    score = hiv4.get_score(tokens)
    scores_content.append(score['Polarity']) # Take only polarity score as proxy for sentiment
    
sc = np.asarray(scores_content)
# Add to validation dataframe
valid['score_content'] = sc
valid.head()

ticker       date     time  \
3174      PM  Feb-04-21  10:33AM   
8657    CTLT  Sep-09-20  10:14AM   
16599    ZTS  Feb-12-21  08:38AM   
5695     AZO  Sep-18-20  06:25AM   
7327     SEE  May-28-20  09:08AM   

                                                headline              news  \
3174   Philip Morris (PM) Q4 Earnings Beat Estimates ...             Zacks   
8657   Radius Completes Enrollment in Phase III Osteo...             Zacks   
16599  Is a Surprise Coming for Zoetis (ZTS) This Ear...             Zacks   
5695   If You Had Bought AutoZone (NYSE:AZO) Shares T...   Simply Wall St.   
7327   Sealed Air (SEE) Stock Down 18% YTD: Will it B...             Zacks   

                                                 content               site  \
3174   Philip Morris International Inc. PM reported f...  finance.yahoo.com   
8657   Radius Health, Inc. RDUS announced the complet...  finance.yahoo.com   
16599  Investors are always looking for stocks that a...  finance.yahoo.com   
5695   The worst result, after buying shares in a com...  finance.yahoo.com   
7327   Sealed Air Corporation’s SEE focus on innovati...  finance.yahoo.com   

       sent     score  score_content  
3174      1 -0.999999       0.428571  
8657      1  0.000000       0.341772  
16599     1  0.999999       0.571429  
5695      1  0.999999       0.622641  
7327      0  0.000000       0.595960

In [23]:
# Calculate correlation between predicted and true 
valid['sent'].corr(valid['score_content'])

0.19840134690097008

In [27]:
# Check if var zero
math.sqrt(variance(valid['score_content']))

0.19356547001409746

In [28]:
# Spearmans correlation coefficient
spearmanr(valid['sent'], valid['score_content'])

SpearmanrResult(correlation=0.03353981625152791, pvalue=0.7404370742610389)

- Notes:
    - Correlation between predicted and true higher using articles

<a id='Maccy'></a>
### Loughran and McDonald Dictionary

#### Using only headlines

In [29]:
lm = ps.LM()
for i in df_news['headline']:
    tokens = lm.tokenize(i)
    score = lm.get_score(tokens)
    print(score)

{'Positive': 0, 'Negative': 2, 'Polarity': -0.99999950000025, 'Subjectivity': 0.1818181652892577}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.33333322222225925}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.24999996875000394}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Sub

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.09999999000000101}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.11111109876543349}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.07692307100591762}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.24999993750001562}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive

{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1,

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'P

...

{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 2, 'Polarity': -0.99999950000025, 'Subjectivity': 0.22222219753086697}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.19999998000000202}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 2, 'Polarity': -0.99999950000025, 'Subjectivity': 0.6666664444445185}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.08333332638888948}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'P

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.24999993750001562}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity

KeyboardInterrupt: 

In [30]:
# Predict sentiment score from labelled data
scores_lm = []
for i in valid['headline']:
    tokens = lm.tokenize(i)
    score = lm.get_score(tokens)
    scores_lm.append(score['Polarity']) # Take only polarity score as proxy for sentiment
    
sc = np.asarray(scores_lm)
# Add to validation dataframe
valid['score_lm'] = sc
valid.head()

ticker       date     time  \
3174      PM  Feb-04-21  10:33AM   
8657    CTLT  Sep-09-20  10:14AM   
16599    ZTS  Feb-12-21  08:38AM   
5695     AZO  Sep-18-20  06:25AM   
7327     SEE  May-28-20  09:08AM   

                                                headline              news  \
3174   Philip Morris (PM) Q4 Earnings Beat Estimates ...             Zacks   
8657   Radius Completes Enrollment in Phase III Osteo...             Zacks   
16599  Is a Surprise Coming for Zoetis (ZTS) This Ear...             Zacks   
5695   If You Had Bought AutoZone (NYSE:AZO) Shares T...   Simply Wall St.   
7327   Sealed Air (SEE) Stock Down 18% YTD: Will it B...             Zacks   

                                                 content               site  \
3174   Philip Morris International Inc. PM reported f...  finance.yahoo.com   
8657   Radius Health, Inc. RDUS announced the complet...  finance.yahoo.com   
16599  Investors are always looking for stocks that a...  finance.yahoo.com   
5695   The worst result, after buying shares in a com...  finance.yahoo.com   
7327   Sealed Air Corporation’s SEE focus on innovati...  finance.yahoo.com   

       sent     score  score_content  score_lm  
3174      1 -0.999999       0.428571       0.0  
8657      1  0.000000       0.341772       0.0  
16599     1  0.999999       0.571429       0.0  
5695      1  0.999999       0.622641       0.0  
7327      0  0.000000       0.595960       0.0

In [31]:
# Calculate correlation between predicted and true 
valid['sent'].corr(valid['score_lm'])

0.10571371353094403

In [36]:
# Spearmans correlation coefficient
spearmanr(valid['sent'], valid['score_lm'])

SpearmanrResult(correlation=0.10542215595379749, pvalue=0.29654112278324607)

#### Articles included

In [32]:
# Predict sentiment score from labelled data
scores_clm = []
for i in valid['content']:
    tokens = lm.tokenize(i)
    score = lm.get_score(tokens)
    scores_clm.append(score['Polarity']) # Take only polarity score as proxy for sentiment
    
sc = np.asarray(scores_clm)
# Add to validation dataframe
valid['score_clm'] = sc
valid.head()

ticker       date     time  \
3174      PM  Feb-04-21  10:33AM   
8657    CTLT  Sep-09-20  10:14AM   
16599    ZTS  Feb-12-21  08:38AM   
5695     AZO  Sep-18-20  06:25AM   
7327     SEE  May-28-20  09:08AM   

                                                headline              news  \
3174   Philip Morris (PM) Q4 Earnings Beat Estimates ...             Zacks   
8657   Radius Completes Enrollment in Phase III Osteo...             Zacks   
16599  Is a Surprise Coming for Zoetis (ZTS) This Ear...             Zacks   
5695   If You Had Bought AutoZone (NYSE:AZO) Shares T...   Simply Wall St.   
7327   Sealed Air (SEE) Stock Down 18% YTD: Will it B...             Zacks   

                                                 content               site  \
3174   Philip Morris International Inc. PM reported f...  finance.yahoo.com   
8657   Radius Health, Inc. RDUS announced the complet...  finance.yahoo.com   
16599  Investors are always looking for stocks that a...  finance.yahoo.com   
5695   The worst result, after buying shares in a com...  finance.yahoo.com   
7327   Sealed Air Corporation’s SEE focus on innovati...  finance.yahoo.com   

       sent     score  score_content  score_lm  score_clm  
3174      1 -0.999999       0.428571       0.0  -0.111111  
8657      1  0.000000       0.341772       0.0   0.333333  
16599     1  0.999999       0.571429       0.0   0.600000  
5695      1  0.999999       0.622641       0.0   0.250000  
7327      0  0.000000       0.595960       0.0  -0.083333

In [33]:
# Calculate correlation between predicted and true 
valid['sent'].corr(valid['score_clm'])

0.3798679935105699

In [37]:
# Spearmans correlation coefficient
spearmanr(valid['sent'], valid['score_clm'])

SpearmanrResult(correlation=0.36014097155177455, pvalue=0.00023283801316179717)

- Notes:
    - Highest correlation using the Loughran and McDonald dictionary, Loughran tailored more for financial applications.